## API 設定

In [1]:
import datetime

In [8]:
nowtime = f'{datetime.datetime.now(): %Y-%m-%d-%H-%M-%S}'
print(nowtime)

 2020-09-15-09-16-58


In [9]:
import twitter

def oauth_login():

    CONSUMER_KEY = 'KOThudX3C7brplSrDa7vSVM2T' #API key 
    CONSUMER_SECRET = 'Fx5shLni0RcK1mPvLkANVbzSmGYK3pUIM0ZfiebpdzCykvVNuA' #API key select
    OAUTH_TOKEN = '109162821-Kh4y6qfclwVBKr8cz978DU7Fz1F0nGs7HiZH34PV'
    OAUTH_TOKEN_SECRET = 'rXd5DKwiAiKQJIBY6o7vH66Od5mQXrHEBP1GEVqoBY9bE'
    
    auth = twitter.oauth.OAuth(OAUTH_TOKEN, OAUTH_TOKEN_SECRET,
                               CONSUMER_KEY, CONSUMER_SECRET)
    
    twitter_api = twitter.Twitter(auth=auth)
    return twitter_api

# Sample usage
twitter_api = oauth_login()    

# Nothing to see by displaying twitter_api except that it's now a
# defined variable

print(twitter_api)

## トレンドを探す

In [10]:
import json
import twitter

def twitter_trends(twitter_api, woe_id):
    # Prefix ID with the underscore for query string parameterization.
    # Without the underscore, the twitter package appends the ID value
    # to the URL itself as a special-case keyword argument.
    return twitter_api.trends.place(_id=woe_id)

# Sample usage

twitter_api = oauth_login()

# See https://dev.twitter.com/docs/api/1.1/get/trends/place and
# http://developer.yahoo.com/geo/geoplanet/ for details on
# Yahoo! Where On Earth ID

WORLD_WOE_ID = 23424856
world_trends = twitter_trends(twitter_api, WORLD_WOE_ID)
print(json.dumps(world_trends, indent=1,ensure_ascii=False))

US_WOE_ID = 1118370
us_trends = twitter_trends(twitter_api, US_WOE_ID)
print(json.dumps(us_trends, indent=1,ensure_ascii=False))

'''都市名	WOEID
Kitakyushu	1110809
Saitama	1116753
Chiba	1117034
Fukuoka	1117099
Hamamatsu	1117155
Hiroshima	1117227
Kawasaki	1117502
Kobe	1117545
Kumamoto	1117605
Nagoya	1117817
Niigata	1117881
Sagamihara	1118072
Sapporo	1118108
Sendai	1118129
Takamatsu	1118285
Tokyo	1118370
Yokohama	1118550
Okinawa	2345896
Osaka	15015370
Kyoto	15015372
Okayama	90036018
Japan	23424856'''

[
 {
  "trends": [
   {
    "name": "最後の搭乗機",
    "url": "http://twitter.com/search?q=%E6%9C%80%E5%BE%8C%E3%81%AE%E6%90%AD%E4%B9%97%E6%A9%9F",
    "promoted_content": null,
    "query": "%E6%9C%80%E5%BE%8C%E3%81%AE%E6%90%AD%E4%B9%97%E6%A9%9F",
    "tweet_volume": null
   },
   {
    "name": "スカラビアCM",
    "url": "http://twitter.com/search?q=%E3%82%B9%E3%82%AB%E3%83%A9%E3%83%93%E3%82%A2CM",
    "promoted_content": null,
    "query": "%E3%82%B9%E3%82%AB%E3%83%A9%E3%83%93%E3%82%A2CM",
    "tweet_volume": 24325
   },
   {
    "name": "ボーテ",
    "url": "http://twitter.com/search?q=%E3%83%9C%E3%83%BC%E3%83%86",
    "promoted_content": null,
    "query": "%E3%83%9C%E3%83%BC%E3%83%86",
    "tweet_volume": 57599
   },
   {
    "name": "#嵐結成21周年",
    "url": "http://twitter.com/search?q=%23%E5%B5%90%E7%B5%90%E6%88%9021%E5%91%A8%E5%B9%B4",
    "promoted_content": null,
    "query": "%23%E5%B5%90%E7%B5%90%E6%88%9021%E5%91%A8%E5%B9%B4",
    "tweet_volume": 38737
   },
   {
    "name": "#ローソンヒノカミチーズ

'都市名\tWOEID\nKitakyushu\t1110809\nSaitama\t1116753\nChiba\t1117034\nFukuoka\t1117099\nHamamatsu\t1117155\nHiroshima\t1117227\nKawasaki\t1117502\nKobe\t1117545\nKumamoto\t1117605\nNagoya\t1117817\nNiigata\t1117881\nSagamihara\t1118072\nSapporo\t1118108\nSendai\t1118129\nTakamatsu\t1118285\nTokyo\t1118370\nYokohama\t1118550\nOkinawa\t2345896\nOsaka\t15015370\nKyoto\t15015372\nOkayama\t90036018\nJapan\t23424856'

## ツィートを検索する

In [11]:
def twitter_search(twitter_api, q, max_results=100, **kw):

    # See https://dev.twitter.com/docs/api/1.1/get/search/tweets and 
    # https://dev.twitter.com/docs/using-search for details on advanced 
    # search criteria that may be useful for keyword arguments
    
    # See https://dev.twitter.com/docs/api/1.1/get/search/tweets    
    search_results = twitter_api.search.tweets(q=q, count=100, **kw)
    
    statuses = search_results['statuses']
    
    # Iterate through batches of results by following the cursor until we
    # reach the desired number of results, keeping in mind that OAuth users
    # can "only" make 180 search queries per 15-minute interval. See
    # https://dev.twitter.com/docs/rate-limiting/1.1/limits
    # for details. A reasonable number of results is ~1000, although
    # that number of results may not exist for all queries.
    
    # Enforce a reasonable limit
    max_results = min(1000, max_results)
    
    for _ in range(10): # 10*100 = 1000
        try:
            next_results = search_results['search_metadata']['next_results']
        except KeyError as e: # No more results when next_results doesn't exist
            break
            
        # Create a dictionary from next_results, which has the following form:
        # ?max_id=313519052523986943&q=NCAA&include_entities=1
        kwargs = dict([ kv.split('=') 
                        for kv in next_results[1:].split("&") ])
        
        search_results = twitter_api.search.tweets(**kwargs)
        statuses += search_results['statuses']
        
        if len(statuses) > max_results: 
            break
            
    return statuses

# Sample usage

twitter_api = oauth_login()

q = "iphone"
results = twitter_search(twitter_api, q, max_results=10,lang='ja')
        
# Show one sample search result by slicing the list...
print(json.dumps(results[0], indent=1,ensure_ascii=False))

{
 "created_at": "Tue Sep 15 00:17:05 +0000 2020",
 "id": 1305661883265871874,
 "id_str": "1305661883265871874",
 "text": "iPhoneのサイドボタン使う時間違ってスクショしちゃうことよくある。",
 "truncated": false,
 "entities": {
  "hashtags": [],
  "symbols": [],
  "user_mentions": [],
  "urls": []
 },
 "metadata": {
  "iso_language_code": "ja",
  "result_type": "recent"
 },
 "source": "<a href=\"http://twitter.com/download/iphone\" rel=\"nofollow\">Twitter for iPhone</a>",
 "in_reply_to_status_id": null,
 "in_reply_to_status_id_str": null,
 "in_reply_to_user_id": null,
 "in_reply_to_user_id_str": null,
 "in_reply_to_screen_name": null,
 "user": {
  "id": 735404224574595072,
  "id_str": "735404224574595072",
  "name": "白餡",
  "screen_name": "siroan1233",
  "location": "",
  "description": "絵を描きます( '༥' )✧",
  "url": "https://t.co/bu1w9IMLgq",
  "entities": {
   "url": {
    "urls": [
     {
      "url": "https://t.co/bu1w9IMLgq",
      "expanded_url": "http://pixiv.net/users/13749935",
      "display_url": "pixiv.net/

## 呼び出し関数の作成

In [12]:
from functools import partial

pp = partial(json.dumps, indent=1,ensure_ascii=False)

twitter_world_trends = partial(twitter_trends, twitter_api, WORLD_WOE_ID)

print(pp(twitter_world_trends()))

authenticated_twitter_search = partial(twitter_search, twitter_api)
results = authenticated_twitter_search("iPhone")
print(pp(results))

authenticated_iphone_twitter_search = partial(authenticated_twitter_search, "iPhone")
results = authenticated_iphone_twitter_search()
print(pp(results))

[
 {
  "trends": [
   {
    "name": "最後の搭乗機",
    "url": "http://twitter.com/search?q=%E6%9C%80%E5%BE%8C%E3%81%AE%E6%90%AD%E4%B9%97%E6%A9%9F",
    "promoted_content": null,
    "query": "%E6%9C%80%E5%BE%8C%E3%81%AE%E6%90%AD%E4%B9%97%E6%A9%9F",
    "tweet_volume": null
   },
   {
    "name": "スカラビアCM",
    "url": "http://twitter.com/search?q=%E3%82%B9%E3%82%AB%E3%83%A9%E3%83%93%E3%82%A2CM",
    "promoted_content": null,
    "query": "%E3%82%B9%E3%82%AB%E3%83%A9%E3%83%93%E3%82%A2CM",
    "tweet_volume": 24325
   },
   {
    "name": "ボーテ",
    "url": "http://twitter.com/search?q=%E3%83%9C%E3%83%BC%E3%83%86",
    "promoted_content": null,
    "query": "%E3%83%9C%E3%83%BC%E3%83%86",
    "tweet_volume": 57599
   },
   {
    "name": "#嵐結成21周年",
    "url": "http://twitter.com/search?q=%23%E5%B5%90%E7%B5%90%E6%88%9021%E5%91%A8%E5%B9%B4",
    "promoted_content": null,
    "query": "%23%E5%B5%90%E7%B5%90%E6%88%9021%E5%91%A8%E5%B9%B4",
    "tweet_volume": 38737
   },
   {
    "name": "#ローソンヒノカミチーズ

[
 {
  "created_at": "Tue Sep 15 00:17:26 +0000 2020",
  "id": 1305661970062831617,
  "id_str": "1305661970062831617",
  "text": "RT @XavierNaxa: Selagi iPhone tersebut tidak diisytiharkan sebagai usang bermakna Apple masih membekalkan alat ganti.\n\nBerikut iPhone yang…",
  "truncated": false,
  "entities": {
   "hashtags": [],
   "symbols": [],
   "user_mentions": [
    {
     "screen_name": "XavierNaxa",
     "name": "Xavier Naxa 🇲🇾",
     "id": 3286689331,
     "id_str": "3286689331",
     "indices": [
      3,
      14
     ]
    }
   ],
   "urls": []
  },
  "metadata": {
   "iso_language_code": "in",
   "result_type": "recent"
  },
  "source": "<a href=\"http://twitter.com/download/iphone\" rel=\"nofollow\">Twitter for iPhone</a>",
  "in_reply_to_status_id": null,
  "in_reply_to_status_id_str": null,
  "in_reply_to_user_id": null,
  "in_reply_to_user_id_str": null,
  "in_reply_to_screen_name": null,
  "user": {
   "id": 847754937421373441,
   "id_str": "847754937421373441",
   "n

[
 {
  "created_at": "Tue Sep 15 00:17:28 +0000 2020",
  "id": 1305661978350776320,
  "id_str": "1305661978350776320",
  "text": "RT @jazz_inmypants: iphone users: good morni—\n\nApple: hey fuckface wanna know how much your ugly ass was staring at the screen last week?…",
  "truncated": false,
  "entities": {
   "hashtags": [],
   "symbols": [],
   "user_mentions": [
    {
     "screen_name": "jazz_inmypants",
     "name": "halsey if you’re reading this hi i’m eli",
     "id": 1020193403882045440,
     "id_str": "1020193403882045440",
     "indices": [
      3,
      18
     ]
    }
   ],
   "urls": []
  },
  "metadata": {
   "iso_language_code": "en",
   "result_type": "recent"
  },
  "source": "<a href=\"http://twitter.com/download/iphone\" rel=\"nofollow\">Twitter for iPhone</a>",
  "in_reply_to_status_id": null,
  "in_reply_to_status_id_str": null,
  "in_reply_to_user_id": null,
  "in_reply_to_user_id_str": null,
  "in_reply_to_screen_name": null,
  "user": {
   "id": 389961897,
  

## JSONデータをテキストで保存する

In [13]:
import io, json

def save_json(filename, data):
    with io.open('resources/ch09-twittercookbook/{0}_{1}.json'.format(filename,nowtime), 
                 'w', encoding='utf-8') as f:
        f.write(json.dumps(data, ensure_ascii=False))

def load_json(filename):
    with io.open('resources/ch09-twittercookbook/{0}_{1}.json'.format(filename,nowtime), 
                 encoding='utf-8') as f:
        return f.read()

# Sample usage

q = '出生前診断'

twitter_api = oauth_login()
results = twitter_search(twitter_api, q, max_results=10,lang='ja')

save_json(q, results)
results = load_json(q)

print(json.dumps(results, indent=1,ensure_ascii=False))

"[{\"created_at\": \"Tue Sep 15 00:16:01 +0000 2020\", \"id\": 1305661615044325376, \"id_str\": \"1305661615044325376\", \"text\": \"出生前診断…どうしようって1人で勝手に悩んだけどやらないことに決めた。\\nたまひよの雑誌読んだら気持ちが落ち着いた！\", \"truncated\": false, \"entities\": {\"hashtags\": [], \"symbols\": [], \"user_mentions\": [], \"urls\": []}, \"metadata\": {\"iso_language_code\": \"ja\", \"result_type\": \"recent\"}, \"source\": \"<a href=\\\"http://twitter.com/download/iphone\\\" rel=\\\"nofollow\\\">Twitter for iPhone</a>\", \"in_reply_to_status_id\": null, \"in_reply_to_status_id_str\": null, \"in_reply_to_user_id\": null, \"in_reply_to_user_id_str\": null, \"in_reply_to_screen_name\": null, \"user\": {\"id\": 1305406352009736194, \"id_str\": \"1305406352009736194\", \"name\": \"ぴーすけ\", \"screen_name\": \"CeIVwLH6ulmPopb\", \"location\": \"\", \"description\": \"パパ27歳💓ママ27歳 結婚2年目💍初マタ🐥予定日2021/3/18✨日々の記録用に🥰予定日の近い方々と繋がれたら嬉しいです🌱無言フォロー失礼します💦\", \"url\": null, \"entities\": {\"description\": {\"urls\": []}}, \"protected\": fal

## MongoDBにJsonデータを保存する

# MongoDBを立ち上げる
https://qiita.com/FukuharaYohei/items/d109f5c3f5dce0d972e4 
- anacondaを立ち上げる前$ 𝑠𝑢𝑑𝑜 𝑠𝑒𝑟𝑣𝑖𝑐𝑒 𝑚𝑜𝑛𝑔𝑜𝑑 𝑠𝑡𝑎𝑟𝑡
- 起動の確認 sudo cat /var/log/mongodb/mongod.log ca

In [9]:
import json
import pymongo # pip install pymongo -> conda install pymongo 

In [10]:
def save_to_mongo(data, mongo_db, mongo_db_coll, **mongo_conn_kw):
    
    # デフォルトでlocalhost:27017 にて実行されているMongoDBサーバに接続
    
    client = pymongo.MongoClient(**mongo_conn_kw)
    
    # 特定のデータベースへの参照を取得する
    
    db = client[mongo_db]
    
    # データベース内の特定のコレクションへの参照を取得する
    
    coll = db[mongo_db_coll]
    
    # バルク挿入を実行してIDを返す
    
    return coll.insert(data)

def load_from_mongo(mongo_db, mongo_db_coll, return_cursor=False,
                    criteria=None, projection=None, **mongo_conn_kw):
    
    # http://docs.mongodb.org/manual/reference/method/db.collection.find/
    #ドキュメントされているように、オプションで選択条件（criteria）と射影条件(projection)
    #を指定して返されるデータを絞り込むことができる
    
    # Consider leveraging MongoDB's aggregations framework for more 
    # sophisticated queries.
    
    client = pymongo.MongoClient(**mongo_conn_kw)
    db = client[mongo_db]
    coll = db[mongo_db_coll]
    
    if criteria is None:
        criteria = {}
    
    if projection is None:
        cursor = coll.find(criteria)
    else:
        cursor = coll.find(criteria, projection)

    # 大量なデータの場合はカーソルを返すと良い
    
    if return_cursor:
        return cursor
    else:
        return [ item for item in cursor ]

In [21]:
# 使用例

q = '出生前診断'

twitter_api = oauth_login()
results = twitter_search(twitter_api, q, max_results=10)

save_to_mongo(results, 'search_results', q)

load_from_mongo('search_results', q)

/home/lcj001/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:18: DeprecationWarning: insert is deprecated. Use insert_one or insert_many instead.


[{'_id': ObjectId('5f572a1061b4b40977416440'),
  'created_at': 'Tue Sep 08 06:46:54 +0000 2020',
  'id': 1303223269575729152,
  'id_str': '1303223269575729152',
  'text': '中絶っていろんな理由って出生前診断の結果もあれば、貧困とか、望まない妊娠、婚約破棄とか、旦那さんとの関係とか\n中絶を簡単に捉えるのは絶対だめだけど、他人の選択にとやかく言うのは違う気がするな😔無理して産んでその後お母さんもその子も幸せならいいけど覚悟がなきゃ子育てなんてできないよ',
  'truncated': False,
  'entities': {'hashtags': [], 'symbols': [], 'user_mentions': [], 'urls': []},
  'metadata': {'iso_language_code': 'ja', 'result_type': 'recent'},
  'source': '<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>',
  'in_reply_to_status_id': 1303220678359838720,
  'in_reply_to_status_id_str': '1303220678359838720',
  'in_reply_to_user_id': 1286179744698871813,
  'in_reply_to_user_id_str': '1286179744698871813',
  'in_reply_to_screen_name': 'an18728874',
  'user': {'id': 1286179744698871813,
   'id_str': '1286179744698871813',
   'name': 'an@初マタ12w',
   'screen_name': 'an18728874',
   'location': '',
   'description': '無言フォロ

## DBの操作
- DBの取得
- コレクションの取得


In [22]:
# DBの取得
client = pymongo.MongoClient()
client.list_database_names()

['admin', 'config', 'local', 'search_results']

In [23]:
#変数、とコレクションの取得
db = client['mongo_db']
collection = db['mongo_db_coll']

## ストリーミングAPIでTwitter Firehouseをサンプリングする

In [27]:
#ストリーミングAPIが提供するフィルタリング機能を使って関心のあるトピックを拾い出す

import sys
import twitter

# 検索する単語

q = '出生前診断' # カンマの検索語

print(sys.stderr, 'Filtering the public timeline for track="%s"' % (q,))
sys.stderr.flush()

twitter_api = oauth_login()

#self.authパラメータのリファレンス
twitter_stream = twitter.TwitterStream(auth=twitter_api.auth)

#  https://dev.twitter.com/docs/streaming-apis　参照
stream = twitter_stream.statuses.filter(track=q)

# For illustrative purposes, when all else fails, search for Justin Bieber
# and something is sure to turn up (at least, on Twitter)

for tweet in stream:
    print(tweet['text'])
    sys.stdout.flush()

    # Save to a database in a particular collection

<ipykernel.iostream.OutStream object at 0x7ff16c61da10> Filtering the public timeline for track="出生前診断"


KeyError: 'text'

## 時系列データを集める

In [ ]:
import sys
import datetime
import time
import twitter

def get_time_series_data(api_func, mongo_db_name, mongo_db_coll, 
                         secs_per_interval=60, max_intervals=15, **mongo_conn_kw):
    
    # 15のインターバルとインターバルごとに1度のAPI呼び出しというデフォルトの
    # 設定を行えば、Twitterのアクセス制限を超えない
    
    interval = 0
    
    while True:
    
        # A timestamp of the form "2013-06-14 12:52:07"
        now = str(datetime.datetime.now()).split(".")[0]
    
        ids = save_to_mongo(api_func(), mongo_db_name, mongo_db_coll + "-" + now)
    
        print(sys.stderr, "Write {0} trends".format(len(ids)))
        print(sys.stderr, "Zzz...")
        print(sys.stderr.flush())
    
        time.sleep(secs_per_interval) # seconds
        interval += 1
        
        if interval >= 15:
            break
        
# Sample usage

get_time_series_data(twitter_world_trends, 'time-series', 'twitter_world_trends')

## Example 10. Extracting tweet entities

In [ ]:
def extract_tweet_entities(statuses):
    
    # See https://dev.twitter.com/docs/tweet-entities for more details on tweet
    # entities

    if len(statuses) == 0:
        return [], [], [], [], []
    
    screen_names = [ user_mention['screen_name'] 
                         for status in statuses
                            for user_mention in status['entities']['user_mentions'] ]
    
    hashtags = [ hashtag['text'] 
                     for status in statuses 
                        for hashtag in status['entities']['hashtags'] ]

    urls = [ url['expanded_url'] 
                     for status in statuses 
                        for url in status['entities']['urls'] ]
    
    symbols = [ symbol['text']
                   for status in statuses
                       for symbol in status['entities']['symbols'] ]
               
    # In some circumstances (such as search results), the media entity
    # may not appear
    if status['entities'].has_key('media'): 
        media = [ media['url'] 
                         for status in statuses  
                            for media in status['entities']['media'] ]
    else:
        media = []

    return screen_names, hashtags, urls, media, symbols

# Sample usage

q = 'CrossFit'

statuses = twitter_search(twitter_api, q)

screen_names, hashtags, urls, media, symbols = extract_tweet_entities(statuses)
    
# Explore the first five items for each...

print json.dumps(screen_names[0:5], indent=1) 
print json.dumps(hashtags[0:5], indent=1)
print json.dumps(urls[0:5], indent=1)
print json.dumps(media[0:5], indent=1)
print json.dumps(symbols[0:5], indent=1)

## Example 11. Finding the most popular tweets in a collection of tweets

In [ ]:
import twitter

def find_popular_tweets(twitter_api, statuses, retweet_threshold=3):

    # You could also consider using the favorite_count parameter as part of 
    # this  heuristic, possibly using it to provide an additional boost to 
    # popular tweets in a ranked formulation
        
    return [ status
                for status in statuses 
                    if status['retweet_count'] > retweet_threshold ] 
    
# Sample usage

q = "CrossFit"

twitter_api = oauth_login()
search_results = twitter_search(twitter_api, q, max_results=200)

popular_tweets = find_popular_tweets(twitter_api, search_results)

for tweet in popular_tweets:
    print tweet['text'], tweet['retweet_count']

## Example 12. Finding the most popular tweet entities in a collection of tweets

In [ ]:
import twitter
from collections import Counter

def get_common_tweet_entities(statuses, entity_threshold=3):

    # Create a flat list of all tweet entities
    tweet_entities = [  e
                        for status in statuses
                            for entity_type in extract_tweet_entities([status]) 
                                for e in entity_type 
                     ]

    c = Counter(tweet_entities).most_common()

    # Compute frequencies
    return [ (k,v) 
             for (k,v) in c
                 if v >= entity_threshold
           ]

# Sample usage

q = 'CrossFit'

twitter_api = oauth_login()
search_results = twitter_search(twitter_api, q, max_results=100)
common_entities = get_common_tweet_entities(search_results)

print "Most common tweet entities"
print common_entities

## Example 13. Tabulating frequency analysis

In [ ]:
from prettytable import PrettyTable

# Get some frequency data

twitter_api = oauth_login()
search_results = twitter_search(twitter_api, q, max_results=100)
common_entities = get_common_tweet_entities(search_results)

# Use PrettyTable to create a nice tabular display

pt = PrettyTable(field_names=['Entity', 'Count']) 
[ pt.add_row(kv) for kv in common_entities ]
pt.align['Entity'], pt.align['Count'] = 'l', 'r' # Set column alignment
print pt

## Example 14. Finding users who have retweeted a status

In [ ]:
import twitter

twitter_api = oauth_login()

print """User IDs for retweeters of a tweet by @fperez_org
that was retweeted by @SocialWebMining and that @jyeee then retweeted
from @SocialWebMining's timeline\n"""
print twitter_api.statuses.retweeters.ids(_id=334188056905129984)['ids']
print json.dumps(twitter_api.statuses.show(_id=334188056905129984), indent=1)
print

print "@SocialWeb's retweet of @fperez_org's tweet\n"
print twitter_api.statuses.retweeters.ids(_id=345723917798866944)['ids']
print json.dumps(twitter_api.statuses.show(_id=345723917798866944), indent=1)
print

print "@jyeee's retweet of @fperez_org's tweet\n"
print twitter_api.statuses.retweeters.ids(_id=338835939172417537)['ids']
print json.dumps(twitter_api.statuses.show(_id=338835939172417537), indent=1)

## Example 15. Extracting a retweet's attribution

In [ ]:
import re

def get_rt_attributions(tweet):

    # Regex adapted from Stack Overflow (http://bit.ly/1821y0J)

    rt_patterns = re.compile(r"(RT|via)((?:\b\W*@\w+)+)", re.IGNORECASE)
    rt_attributions = []

    # Inspect the tweet to see if it was produced with /statuses/retweet/:id.
    # See https://dev.twitter.com/docs/api/1.1/get/statuses/retweets/%3Aid.
    
    if tweet.has_key('retweeted_status'):
        attribution = tweet['retweeted_status']['user']['screen_name'].lower()
        rt_attributions.append(attribution)

    # Also, inspect the tweet for the presence of "legacy" retweet patterns
    # such as "RT" and "via", which are still widely used for various reasons
    # and potentially very useful. See https://dev.twitter.com/discussions/2847 
    # and https://dev.twitter.com/discussions/1748 for some details on how/why.

    try:
        rt_attributions += [ 
                        mention.strip() 
                        for mention in rt_patterns.findall(tweet['text'])[0][1].split() 
                      ]
    except IndexError, e:
        pass

    # Filter out any duplicates

    return list(set([rta.strip("@").lower() for rta in rt_attributions]))

# Sample usage
twitter_api = oauth_login()

tweet = twitter_api.statuses.show(_id=214746575765913602)
print get_rt_attributions(tweet)
print
tweet = twitter_api.statuses.show(_id=345723917798866944)
print get_rt_attributions(tweet)

## Example 16. Making robust Twitter requests

In [ ]:
import sys
import time
from urllib2 import URLError
from httplib import BadStatusLine
import json
import twitter

def make_twitter_request(twitter_api_func, max_errors=10, *args, **kw): 
    
    # A nested helper function that handles common HTTPErrors. Return an updated
    # value for wait_period if the problem is a 500 level error. Block until the
    # rate limit is reset if it's a rate limiting issue (429 error). Returns None
    # for 401 and 404 errors, which requires special handling by the caller.
    def handle_twitter_http_error(e, wait_period=2, sleep_when_rate_limited=True):
    
        if wait_period > 3600: # Seconds
            print >> sys.stderr, 'Too many retries. Quitting.'
            raise e
    
        # See https://dev.twitter.com/docs/error-codes-responses for common codes
    
        if e.e.code == 401:
            print >> sys.stderr, 'Encountered 401 Error (Not Authorized)'
            return None
        elif e.e.code == 404:
            print >> sys.stderr, 'Encountered 404 Error (Not Found)'
            return None
        elif e.e.code == 429: 
            print >> sys.stderr, 'Encountered 429 Error (Rate Limit Exceeded)'
            if sleep_when_rate_limited:
                print >> sys.stderr, "Retrying in 15 minutes...ZzZ..."
                sys.stderr.flush()
                time.sleep(60*15 + 5)
                print >> sys.stderr, '...ZzZ...Awake now and trying again.'
                return 2
            else:
                raise e # Caller must handle the rate limiting issue
        elif e.e.code in (500, 502, 503, 504):
            print >> sys.stderr, 'Encountered %i Error. Retrying in %i seconds' % \
                (e.e.code, wait_period)
            time.sleep(wait_period)
            wait_period *= 1.5
            return wait_period
        else:
            raise e

    # End of nested helper function
    
    wait_period = 2 
    error_count = 0 

    while True:
        try:
            return twitter_api_func(*args, **kw)
        except twitter.api.TwitterHTTPError, e:
            error_count = 0 
            wait_period = handle_twitter_http_error(e, wait_period)
            if wait_period is None:
                return
        except URLError, e:
            error_count += 1
            time.sleep(wait_period)
            wait_period *= 1.5
            print >> sys.stderr, "URLError encountered. Continuing."
            if error_count > max_errors:
                print >> sys.stderr, "Too many consecutive errors...bailing out."
                raise
        except BadStatusLine, e:
            error_count += 1
            time.sleep(wait_period)
            wait_period *= 1.5
            print >> sys.stderr, "BadStatusLine encountered. Continuing."
            if error_count > max_errors:
                print >> sys.stderr, "Too many consecutive errors...bailing out."
                raise

# Sample usage

twitter_api = oauth_login()

# See https://dev.twitter.com/docs/api/1.1/get/users/lookup for 
# twitter_api.users.lookup

response = make_twitter_request(twitter_api.users.lookup, 
                                screen_name="SocialWebMining")

print json.dumps(response, indent=1)

## Example 17. Resolving user profile information

In [ ]:
def get_user_profile(twitter_api, screen_names=None, user_ids=None):
   
    # Must have either screen_name or user_id (logical xor)
    assert (screen_names != None) != (user_ids != None), \
    "Must have screen_names or user_ids, but not both"
    
    items_to_info = {}

    items = screen_names or user_ids
    
    while len(items) > 0:

        # Process 100 items at a time per the API specifications for /users/lookup.
        # See https://dev.twitter.com/docs/api/1.1/get/users/lookup for details.
        
        items_str = ','.join([str(item) for item in items[:100]])
        items = items[100:]

        if screen_names:
            response = make_twitter_request(twitter_api.users.lookup, 
                                            screen_name=items_str)
        else: # user_ids
            response = make_twitter_request(twitter_api.users.lookup, 
                                            user_id=items_str)
    
        for user_info in response:
            if screen_names:
                items_to_info[user_info['screen_name']] = user_info
            else: # user_ids
                items_to_info[user_info['id']] = user_info

    return items_to_info

# Sample usage

twitter_api = oauth_login()

print get_user_profile(twitter_api, screen_names=["SocialWebMining", "ptwobrussell"]) 
#print get_user_profile(twitter_api, user_ids=[132373965])

## Example 18. Extracting tweet entities from arbitrary text

In [ ]:
import twitter_text

# Sample usage

txt = "RT @SocialWebMining Mining 1M+ Tweets About #Syria http://wp.me/p3QiJd-1I"

ex = twitter_text.Extractor(txt)

print "Screen Names:", ex.extract_mentioned_screen_names_with_indices()
print "URLs:", ex.extract_urls_with_indices()
print "Hashtags:", ex.extract_hashtags_with_indices()

## Example 19. Getting all friends or followers for a user

In [ ]:
from functools import partial
from sys import maxint

def get_friends_followers_ids(twitter_api, screen_name=None, user_id=None,
                              friends_limit=maxint, followers_limit=maxint):
    
    # Must have either screen_name or user_id (logical xor)
    assert (screen_name != None) != (user_id != None), \
    "Must have screen_name or user_id, but not both"
    
    # See https://dev.twitter.com/docs/api/1.1/get/friends/ids and
    # https://dev.twitter.com/docs/api/1.1/get/followers/ids for details
    # on API parameters
    
    get_friends_ids = partial(make_twitter_request, twitter_api.friends.ids, 
                              count=5000)
    get_followers_ids = partial(make_twitter_request, twitter_api.followers.ids, 
                                count=5000)

    friends_ids, followers_ids = [], []
    
    for twitter_api_func, limit, ids, label in [
                    [get_friends_ids, friends_limit, friends_ids, "friends"], 
                    [get_followers_ids, followers_limit, followers_ids, "followers"]
                ]:
        
        if limit == 0: continue
        
        cursor = -1
        while cursor != 0:
        
            # Use make_twitter_request via the partially bound callable...
            if screen_name: 
                response = twitter_api_func(screen_name=screen_name, cursor=cursor)
            else: # user_id
                response = twitter_api_func(user_id=user_id, cursor=cursor)

            if response is not None:
                ids += response['ids']
                cursor = response['next_cursor']
        
            print >> sys.stderr, 'Fetched {0} total {1} ids for {2}'.format(len(ids), 
                                                    label, (user_id or screen_name))
        
            # XXX: You may want to store data during each iteration to provide an 
            # an additional layer of protection from exceptional circumstances
        
            if len(ids) >= limit or response is None:
                break

    # Do something useful with the IDs, like store them to disk...
    return friends_ids[:friends_limit], followers_ids[:followers_limit]

# Sample usage

twitter_api = oauth_login()

friends_ids, followers_ids = get_friends_followers_ids(twitter_api, 
                                                       screen_name="SocialWebMining", 
                                                       friends_limit=10, 
                                                       followers_limit=10)

print friends_ids
print followers_ids

## Example 20. Analyzing a user's friends and followers

In [ ]:
def setwise_friends_followers_analysis(screen_name, friends_ids, followers_ids):
    
    friends_ids, followers_ids = set(friends_ids), set(followers_ids)
    
    print '{0} is following {1}'.format(screen_name, len(friends_ids))

    print '{0} is being followed by {1}'.format(screen_name, len(followers_ids))
    
    print '{0} of {1} are not following {2} back'.format(
            len(friends_ids.difference(followers_ids)), 
            len(friends_ids), screen_name)
    
    print '{0} of {1} are not being followed back by {2}'.format(
            len(followers_ids.difference(friends_ids)), 
            len(followers_ids), screen_name)
    
    print '{0} has {1} mutual friends'.format(
            screen_name, len(friends_ids.intersection(followers_ids)))

# Sample usage

screen_name = "ptwobrussell"

twitter_api = oauth_login()

friends_ids, followers_ids = get_friends_followers_ids(twitter_api, 
                                                       screen_name=screen_name)
setwise_friends_followers_analysis(screen_name, friends_ids, followers_ids)

## Example 21. Harvesting a user's tweets

In [ ]:
def harvest_user_timeline(twitter_api, screen_name=None, user_id=None, max_results=1000):
     
    assert (screen_name != None) != (user_id != None), \
    "Must have screen_name or user_id, but not both"    
    
    kw = {  # Keyword args for the Twitter API call
        'count': 200,
        'trim_user': 'true',
        'include_rts' : 'true',
        'since_id' : 1
        }
    
    if screen_name:
        kw['screen_name'] = screen_name
    else:
        kw['user_id'] = user_id
        
    max_pages = 16
    results = []
    
    tweets = make_twitter_request(twitter_api.statuses.user_timeline, **kw)
    
    if tweets is None: # 401 (Not Authorized) - Need to bail out on loop entry
        tweets = []
        
    results += tweets
    
    print >> sys.stderr, 'Fetched %i tweets' % len(tweets)
    
    page_num = 1
    
    # Many Twitter accounts have fewer than 200 tweets so you don't want to enter
    # the loop and waste a precious request if max_results = 200.
    
    # Note: Analogous optimizations could be applied inside the loop to try and 
    # save requests. e.g. Don't make a third request if you have 287 tweets out of 
    # a possible 400 tweets after your second request. Twitter does do some 
    # post-filtering on censored and deleted tweets out of batches of 'count', though,
    # so you can't strictly check for the number of results being 200. You might get
    # back 198, for example, and still have many more tweets to go. If you have the
    # total number of tweets for an account (by GET /users/lookup/), then you could 
    # simply use this value as a guide.
    
    if max_results == kw['count']:
        page_num = max_pages # Prevent loop entry
    
    while page_num < max_pages and len(tweets) > 0 and len(results) < max_results:
    
        # Necessary for traversing the timeline in Twitter's v1.1 API:
        # get the next query's max-id parameter to pass in.
        # See https://dev.twitter.com/docs/working-with-timelines.
        kw['max_id'] = min([ tweet['id'] for tweet in tweets]) - 1 
    
        tweets = make_twitter_request(twitter_api.statuses.user_timeline, **kw)
        results += tweets

        print >> sys.stderr, 'Fetched %i tweets' % (len(tweets),)
    
        page_num += 1
        
    print >> sys.stderr, 'Done fetching tweets'

    return results[:max_results]
    
# Sample usage

twitter_api = oauth_login()
tweets = harvest_user_timeline(twitter_api, screen_name="SocialWebMining", \
                               max_results=200)

# Save to MongoDB with save_to_mongo or a local file with save_json...

## Example 22. Crawling a friendship graph

In [ ]:
def crawl_followers(twitter_api, screen_name, limit=1000000, depth=2):
    
    # Resolve the ID for screen_name and start working with IDs for consistency 
    # in storage

    seed_id = str(twitter_api.users.show(screen_name=screen_name)['id'])
    
    _, next_queue = get_friends_followers_ids(twitter_api, user_id=seed_id, 
                                              friends_limit=0, followers_limit=limit)

    # Store a seed_id => _follower_ids mapping in MongoDB
    
    save_to_mongo({'followers' : [ _id for _id in next_queue ]}, 'followers_crawl', 
                  '{0}-follower_ids'.format(seed_id))
    
    d = 1
    while d < depth:
        d += 1
        (queue, next_queue) = (next_queue, [])
        for fid in queue:
            _, follower_ids = get_friends_followers_ids(twitter_api, user_id=fid, 
                                                     friends_limit=0, 
                                                     followers_limit=limit)
            
            # Store a fid => follower_ids mapping in MongoDB
            save_to_mongo({'followers' : [ _id for _id in follower_ids ]}, 
                          'followers_crawl', '{0}-follower_ids'.format(fid))
            
            next_queue += follower_ids

# Sample usage

screen_name = "timoreilly"

twitter_api = oauth_login()

crawl_followers(twitter_api, screen_name, depth=1, limit=10)

## Example 23. Analyzing tweet content

In [ ]:
def analyze_tweet_content(statuses):
    
    if len(statuses) == 0:
        print "No statuses to analyze"
        return
    
    # A nested helper function for computing lexical diversity
    def lexical_diversity(tokens):
        return 1.0*len(set(tokens))/len(tokens) 
    
    # A nested helper function for computing the average number of words per tweet
    def average_words(statuses):
        total_words = sum([ len(s.split()) for s in statuses ]) 
        return 1.0*total_words/len(statuses)

    status_texts = [ status['text'] for status in statuses ]
    screen_names, hashtags, urls, media, _ = extract_tweet_entities(statuses)
    
    # Compute a collection of all words from all tweets
    words = [ w 
          for t in status_texts 
              for w in t.split() ]
    
    print "Lexical diversity (words):", lexical_diversity(words)
    print "Lexical diversity (screen names):", lexical_diversity(screen_names)
    print "Lexical diversity (hashtags):", lexical_diversity(hashtags)
    print "Averge words per tweet:", average_words(status_texts)

    
# Sample usage

q = 'CrossFit'
twitter_api = oauth_login()
search_results = twitter_search(twitter_api, q)

analyze_tweet_content(search_results)

## Example 24. Summarizing link targets

In [ ]:
import sys
import json
import nltk
import numpy
import requests
from boilerpipe.extract import Extractor

def summarize(url=None, html=None, n=100, cluster_threshold=5, top_sentences=5):

    # Adapted from "The Automatic Creation of Literature Abstracts" by H.P. Luhn
    #
    # Parameters:
    # * n  - Number of words to consider
    # * cluster_threshold - Distance between words to consider
    # * top_sentences - Number of sentences to return for a "top n" summary
            
    # Begin - nested helper function
    def score_sentences(sentences, important_words):
        scores = []
        sentence_idx = -1
    
        for s in [nltk.tokenize.word_tokenize(s) for s in sentences]:
    
            sentence_idx += 1
            word_idx = []
    
            # For each word in the word list...
            for w in important_words:
                try:
                    # Compute an index for important words in each sentence
    
                    word_idx.append(s.index(w))
                except ValueError, e: # w not in this particular sentence
                    pass
    
            word_idx.sort()
    
            # It is possible that some sentences may not contain any important words
            if len(word_idx)== 0: continue
    
            # Using the word index, compute clusters with a max distance threshold
            # for any two consecutive words
    
            clusters = []
            cluster = [word_idx[0]]
            i = 1
            while i < len(word_idx):
                if word_idx[i] - word_idx[i - 1] < cluster_threshold:
                    cluster.append(word_idx[i])
                else:
                    clusters.append(cluster[:])
                    cluster = [word_idx[i]]
                i += 1
            clusters.append(cluster)
    
            # Score each cluster. The max score for any given cluster is the score 
            # for the sentence.
    
            max_cluster_score = 0
            for c in clusters:
                significant_words_in_cluster = len(c)
                total_words_in_cluster = c[-1] - c[0] + 1
                score = 1.0 * significant_words_in_cluster \
                    * significant_words_in_cluster / total_words_in_cluster
    
                if score > max_cluster_score:
                    max_cluster_score = score
    
            scores.append((sentence_idx, score))
    
        return scores    
    
    # End - nested helper function
    
    extractor = Extractor(extractor='ArticleExtractor', url=url, html=html)

    # It's entirely possible that this "clean page" will be a big mess. YMMV.
    # The good news is that the summarize algorithm inherently accounts for handling
    # a lot of this noise.

    txt = extractor.getText()
    
    sentences = [s for s in nltk.tokenize.sent_tokenize(txt)]
    normalized_sentences = [s.lower() for s in sentences]

    words = [w.lower() for sentence in normalized_sentences for w in
             nltk.tokenize.word_tokenize(sentence)]

    fdist = nltk.FreqDist(words)

    top_n_words = [w[0] for w in fdist.items() 
            if w[0] not in nltk.corpus.stopwords.words('english')][:n]

    scored_sentences = score_sentences(normalized_sentences, top_n_words)

    # Summarization Approach 1:
    # Filter out nonsignificant sentences by using the average score plus a
    # fraction of the std dev as a filter

    avg = numpy.mean([s[1] for s in scored_sentences])
    std = numpy.std([s[1] for s in scored_sentences])
    mean_scored = [(sent_idx, score) for (sent_idx, score) in scored_sentences
                   if score > avg + 0.5 * std]

    # Summarization Approach 2:
    # Another approach would be to return only the top N ranked sentences

    top_n_scored = sorted(scored_sentences, key=lambda s: s[1])[-top_sentences:]
    top_n_scored = sorted(top_n_scored, key=lambda s: s[0])

    # Decorate the post object with summaries

    return dict(top_n_summary=[sentences[idx] for (idx, score) in top_n_scored],
                mean_scored_summary=[sentences[idx] for (idx, score) in mean_scored])

# Sample usage

sample_url = 'http://radar.oreilly.com/2013/06/phishing-in-facebooks-pond.html'
summary = summarize(url=sample_url)

# Alternatively, you can pass in HTML if you have it. Sometimes this approach may be
# necessary if you encounter mysterious urllib2.BadStatusLine errors. Here's how
# that would work:

# sample_html = requests.get(sample_url).text
# summary = summarize(html=sample_html)

print "-------------------------------------------------"
print "                'Top N Summary'"
print "-------------------------------------------------"
print " ".join(summary['top_n_summary'])
print
print
print "-------------------------------------------------"
print "             'Mean Scored' Summary"
print "-------------------------------------------------"
print " ".join(summary['mean_scored_summary'])

## Example 25. Analyzing a user's favorite tweets

In [ ]:

def analyze_favorites(twitter_api, screen_name, entity_threshold=2):
    
    # Could fetch more than 200 by walking the cursor as shown in other
    # recipes, but 200 is a good sample to work with.
    favs = twitter_api.favorites.list(screen_name=screen_name, count=200)
    print "Number of favorites:", len(favs)
    
    # Figure out what some of the common entities are, if any, in the content
    
    common_entities = get_common_tweet_entities(favs, 
                                                entity_threshold=entity_threshold)
    
    # Use PrettyTable to create a nice tabular display
    
    pt = PrettyTable(field_names=['Entity', 'Count']) 
    [ pt.add_row(kv) for kv in common_entities ]
    pt.align['Entity'], pt.align['Count'] = 'l', 'r' # Set column alignment
    
    print
    print "Common entities in favorites..."
    print pt
    
    
    # Print out some other stats
    print
    print "Some statistics about the content of the favorities..."
    print
    analyze_tweet_content(favs)
    
    # Could also start analyzing link content or summarized link content, and more.

# Sample usage

twitter_api = oauth_login()
analyze_favorites(twitter_api, "ptwobrussell")